In [ ]:
from huggingface_hub import notebook_login
notebook_login()

In [1]:
from datasets import load_dataset, DatasetDict

In [2]:
minds14_train = load_dataset(
    "PolyAI/minds14", 
    "en-US",
    split="train"
)
minds14_train

Dataset({
    features: ['path', 'audio', 'transcription', 'english_transcription', 'intent_class', 'lang_id'],
    num_rows: 563
})

In [3]:
minds14 = DatasetDict()

minds14["train"] = minds14_train.select(range(450))
minds14["test"] = minds14_train.select(range(450, 563))

minds14

DatasetDict({
    train: Dataset({
        features: ['path', 'audio', 'transcription', 'english_transcription', 'intent_class', 'lang_id'],
        num_rows: 450
    })
    test: Dataset({
        features: ['path', 'audio', 'transcription', 'english_transcription', 'intent_class', 'lang_id'],
        num_rows: 113
    })
})

In [4]:
minds14 = minds14.select_columns(['audio', 'transcription'])
minds14

DatasetDict({
    train: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 450
    })
    test: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 113
    })
})

In [5]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained(
    "openai/whisper-tiny", language="english", task="transcribe"
)

In [6]:
minds14["train"].features

{'audio': Audio(sampling_rate=8000, mono=True, decode=True, id=None),
 'transcription': Value(dtype='string', id=None)}

In [7]:
from datasets import Audio

sampling_rate = processor.feature_extractor.sampling_rate
minds14 = minds14.cast_column("audio", Audio(sampling_rate=sampling_rate))

In [8]:
def prepare_dataset(example):
    audio = example["audio"]

    example = processor(
        audio=audio["array"],
        sampling_rate=audio["sampling_rate"],
        text=example["transcription"],
    )

    # compute input length of audio sample in seconds
    example["input_length"] = len(audio["array"]) / audio["sampling_rate"]

    return example

In [9]:
minds14 = minds14.map(
    prepare_dataset, remove_columns=minds14.column_names["train"], num_proc=1
)

Map:   0%|          | 0/450 [00:00<?, ? examples/s]

Map:   0%|          | 0/113 [00:00<?, ? examples/s]

In [10]:
max_input_length = 30.0
def is_audio_in_length_range(length):
    return length < max_input_length

In [11]:
minds14["train"] = minds14["train"].filter(
    is_audio_in_length_range,
    input_columns=["input_length"],
)

Filter:   0%|          | 0/450 [00:00<?, ? examples/s]

In [12]:
minds14['train']

Dataset({
    features: ['input_features', 'labels', 'input_length'],
    num_rows: 445
})

### Training and Evaluation

In [13]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union


@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(
        self, features: List[Dict[str, Union[List[int], torch.Tensor]]]
    ) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [
            {"input_features": feature["input_features"][0]} for feature in features
        ]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(
            labels_batch.attention_mask.ne(1), -100
        )

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch

In [14]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [15]:
import evaluate
from transformers.models.whisper.english_normalizer import BasicTextNormalizer

metric = evaluate.load("wer")
normalizer = BasicTextNormalizer()

def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = processor.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = processor.batch_decode(label_ids, skip_special_tokens=True)

    # compute orthographic wer
    wer_ortho = 100 * metric.compute(predictions=pred_str, references=label_str)

    # compute normalised WER
    pred_str_norm = [normalizer(pred) for pred in pred_str]
    label_str_norm = [normalizer(label) for label in label_str]
    # filtering step to only evaluate the samples that correspond to non-zero references:
    pred_str_norm = [
        pred_str_norm[i] for i in range(len(pred_str_norm)) if len(label_str_norm[i]) > 0
    ]
    label_str_norm = [
        label_str_norm[i]
        for i in range(len(label_str_norm))
        if len(label_str_norm[i]) > 0
    ]

    wer = 100 * metric.compute(predictions=pred_str_norm, references=label_str_norm)

    return {"wer_ortho": wer_ortho, "wer": wer}

In [16]:
from transformers import WhisperForConditionalGeneration
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-tiny")

In [17]:
from functools import partial

# disable cache during training since it's incompatible with gradient checkpointing
model.config.use_cache = False

# set language and task for generation and re-enable cache
model.generate = partial(
    model.generate, language="english", task="transcribe", use_cache=True
)

In [18]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./whisper-tiny-en-us-minds14",  # name on the HF Hub
    per_device_train_batch_size=16,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    lr_scheduler_type="constant_with_warmup",
    warmup_steps=50,
    max_steps=4000,  # increase to 4000 if you have your own GPU or a Colab paid plan
    gradient_checkpointing=True,
    # fp16=True,
    # fp16_full_eval=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=16,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=500,
    eval_steps=500,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    # push_to_hub=False,
)

In [19]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=minds14["train"],
    eval_dataset=minds14["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor,
)

In [20]:
trainer.train()

  0%|          | 0/4000 [00:00<?, ?it/s]

/Users/mkhojira/Projects/mml/audio-course/venv/lib/python3.8/site-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


{'loss': 1.584, 'learning_rate': 5e-06, 'epoch': 0.89}
{'loss': 0.6567, 'learning_rate': 1e-05, 'epoch': 1.79}
{'loss': 0.1857, 'learning_rate': 1e-05, 'epoch': 2.68}
{'loss': 0.1218, 'learning_rate': 1e-05, 'epoch': 3.57}
{'loss': 0.0876, 'learning_rate': 1e-05, 'epoch': 4.46}
{'loss': 0.0512, 'learning_rate': 1e-05, 'epoch': 5.36}
{'loss': 0.0299, 'learning_rate': 1e-05, 'epoch': 6.25}
{'loss': 0.016, 'learning_rate': 1e-05, 'epoch': 7.14}
{'loss': 0.0085, 'learning_rate': 1e-05, 'epoch': 8.04}
{'loss': 0.0038, 'learning_rate': 1e-05, 'epoch': 8.93}
{'loss': 0.0028, 'learning_rate': 1e-05, 'epoch': 9.82}
{'loss': 0.0023, 'learning_rate': 1e-05, 'epoch': 10.71}
{'loss': 0.0015, 'learning_rate': 1e-05, 'epoch': 11.61}
{'loss': 0.0012, 'learning_rate': 1e-05, 'epoch': 12.5}
{'loss': 0.0011, 'learning_rate': 1e-05, 'epoch': 13.39}
{'loss': 0.0009, 'learning_rate': 1e-05, 'epoch': 14.29}
{'loss': 0.0008, 'learning_rate': 1e-05, 'epoch': 15.18}
{'loss': 0.0007, 'learning_rate': 1e-05, 'epo

  0%|          | 0/8 [00:00<?, ?it/s]

{'eval_loss': 0.25609758496284485, 'eval_wer_ortho': 35.90376310919186, 'eval_wer': 35.30106257378985, 'eval_runtime': 27.7439, 'eval_samples_per_second': 4.073, 'eval_steps_per_second': 0.288, 'epoch': 17.86}


...

  0%|          | 0/8 [00:00<?, ?it/s]

{'eval_loss': 0.3247106671333313, 'eval_wer_ortho': 36.705737199259715, 'eval_wer': 36.658795749704844, 'eval_runtime': 20.5021, 'eval_samples_per_second': 5.512, 'eval_steps_per_second': 0.39, 'epoch': 107.14}


/Users/mkhojira/Projects/mml/audio-course/venv/lib/python3.8/site-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 108.04}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 108.93}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 109.82}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 110.71}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 111.61}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 112.5}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 113.39}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 114.29}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 115.18}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 116.07}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 116.96}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 117.86}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 118.75}
{'loss': 0.0, 'learning_rate': 1e-05, 'epoch': 119.64}


KeyboardInterrupt: 

In [ ]:
# from transformers import GenerationConfig
# generation_config = GenerationConfig.from_pretrained("openai/whisper-tiny.en")
# generation_config.push_to_hub('mirodil/whisper-tiny-en-us-minds14')

In [21]:
kwargs = {
    "dataset_tags": "PolyAI/minds14",
    "finetuned_from": "openai/whisper-tiny",
    "tasks": "automatic-speech-recognition",
}
trainer.push_to_hub(**kwargs)

events.out.tfevents.1700719599.L67DDV9G7R.91939.0:   0%|          | 0.00/29.3k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/151M [00:00<?, ?B/s]

training_args.bin:   0%|          | 0.00/4.73k [00:00<?, ?B/s]

Upload 3 LFS files:   0%|          | 0/3 [00:00<?, ?it/s]

'https://huggingface.co/mirodil/whisper-tiny-en-us-minds14/tree/main/'

In [ ]:
model.generation_config

In [ ]:
hasattr(generation_config, "lang_to_id")